In [26]:
!pip install nltk
!pip install tensorflow

In [27]:
import pandas as pd
import numpy as np
import re
import string
import nltk
from nltk.tokenize import sent_tokenize # tries to convert paragraph to sentences
from nltk.tokenize import word_tokenize
from nltk.stem import WordNetLemmatizer
from nltk.corpus import stopwords
from gensim.models import Word2Vec
import ast
import tensorflow as tf
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder
from keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, Dropout, LSTM, Embedding
from tensorflow.keras.metrics import MeanAbsoluteError
from sklearn.metrics import r2_score

nltk.download('punkt')

[nltk_data] Downloading package punkt to
[nltk_data]     /Users/preethamreddygollapalli/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


True

In [28]:
df = pd.read_csv("/Users/preethamreddygollapalli/Downloads/AI Test cases (2).csv")
df.head(5)

Story Name                      Test case Acceptance criteria  \
0  ACIP-247941  Weekly Ad - tap on any product offer - tap on ...   
1   ACIP-95038  As a PdM, I want to ensure that the L2 entry p...   
2     US-41769  As a customer, I should see age restriction me...   
3  ACIP-237923  Verify Banner navigation for the below banners...   
4  ACIP-234885  Display the Meal Plans banner based on the ban...   

                                          Test Steps  \
0  User logs into UMA application with valid user...   
1  Login UMA app with valid email/ mobile no. Ver...   
2  Login UMA app with valid email/ mobile no. Ent...   
3  User logs into UMA application with valid user...   
4  User logs into UMA application with valid user...   

                                           Test Data  \
0  Email: dnfcontentqa2_2@mail7.io, Albertsons= 8...   
1                                                NaN   
2                                                NaN   
3  Email: dnfcontentqa2_2@mail7.io, Albertsons= 8...   
4  Email: dnfcontentqa2_2@mail7.io / any new user...   

                                     Expected Result  
0  User navigates to Home page on UMA application...  
1  User should be able to login successfully and ...  
2  Your order contains age-restricted items. Some...  
3  User navigates to Home page on UMA application...  
4  User navigates to Home page on UMA application...

In [29]:
df.dtypes

Story Name                       object
Test case Acceptance criteria    object
Test Steps                       object
Test Data                        object
Expected Result                  object
dtype: object

In [30]:
df.shape

(5, 5)

In [31]:
df.describe()

Story Name                      Test case Acceptance criteria  \
count             5                                                  5   
unique            5                                                  5   
top     ACIP-247941  Weekly Ad - tap on any product offer - tap on ...   
freq              1                                                  1   

                                               Test Steps  \
count                                                   5   
unique                                                  5   
top     User logs into UMA application with valid user...   
freq                                                    1   

                                                Test Data  \
count                                                   3   
unique                                                  3   
top     Email: dnfcontentqa2_2@mail7.io, Albertsons= 8...   
freq                                                    1   

                                          Expected Result  
count                                                   5  
unique                                                  5  
top     User navigates to Home page on UMA application...  
freq                                                    1

In [32]:
df = df.drop(['Story Name', 'Test Data'], axis = 1)
df.head(5)

Test case Acceptance criteria  \
0  Weekly Ad - tap on any product offer - tap on ...   
1  As a PdM, I want to ensure that the L2 entry p...   
2  As a customer, I should see age restriction me...   
3  Verify Banner navigation for the below banners...   
4  Display the Meal Plans banner based on the ban...   

                                          Test Steps  \
0  User logs into UMA application with valid user...   
1  Login UMA app with valid email/ mobile no. Ver...   
2  Login UMA app with valid email/ mobile no. Ent...   
3  User logs into UMA application with valid user...   
4  User logs into UMA application with valid user...   

                                     Expected Result  
0  User navigates to Home page on UMA application...  
1  User should be able to login successfully and ...  
2  Your order contains age-restricted items. Some...  
3  User navigates to Home page on UMA application...  
4  User navigates to Home page on UMA application...

In [9]:
# Tokenize the strings by splitting on spaces
df['Test_case_Acceptance_criteria'] = df['Test case Acceptance criteria'].apply(lambda x: x.split() if isinstance(x, str) else [])
df['Test_Steps'] = df['Test Steps'].apply(lambda x: x.split() if isinstance(x, str) else [])
df['Expected_Result'] = df['Expected Result'].apply(lambda x: x.split() if isinstance(x, str) else [])

# Inspect the tokenized data
df.head(5)

Test case Acceptance criteria  \
0  Weekly Ad - tap on any product offer - tap on ...   
1  As a PdM, I want to ensure that the L2 entry p...   
2  As a customer, I should see age restriction me...   
3  Verify Banner navigation for the below banners...   
4  Display the Meal Plans banner based on the ban...   

                                          Test Steps  \
0  User logs into UMA application with valid user...   
1  Login UMA app with valid email/ mobile no. Ver...   
2  Login UMA app with valid email/ mobile no. Ent...   
3  User logs into UMA application with valid user...   
4  User logs into UMA application with valid user...   

                                     Expected Result  \
0  User navigates to Home page on UMA application...   
1  User should be able to login successfully and ...   
2  Your order contains age-restricted items. Some...   
3  User navigates to Home page on UMA application...   
4  User navigates to Home page on UMA application...   

                       Test_case_Acceptance_criteria  \
0  [Weekly, Ad, -, tap, on, any, product, offer, ...   
1  [As, a, PdM,, I, want, to, ensure, that, the, ...   
2  [As, a, customer,, I, should, see, age, restri...   
3  [Verify, Banner, navigation, for, the, below, ...   
4  [Display, the, Meal, Plans, banner, based, on,...   

                                          Test_Steps  \
0  [User, logs, into, UMA, application, with, val...   
1  [Login, UMA, app, with, valid, email/, mobile,...   
2  [Login, UMA, app, with, valid, email/, mobile,...   
3  [User, logs, into, UMA, application, with, val...   
4  [User, logs, into, UMA, application, with, val...   

                                     Expected_Result  
0  [User, navigates, to, Home, page, on, UMA, app...  
1  [User, should, be, able, to, login, successful...  
2  [Your, order, contains, age-restricted, items....  
3  [User, navigates, to, Home, page, on, UMA, app...  
4  [User, navigates, to, Home, page, on, UMA, app...

In [10]:
print(df.isna().sum())

Test case Acceptance criteria    0
Test Steps                       0
Expected Result                  0
Test_case_Acceptance_criteria    0
Test_Steps                       0
Expected_Result                  0
dtype: int64


In [11]:
df = df.drop(['Test case Acceptance criteria', 'Test Steps', 'Expected Result'], axis = 1)
df.head(5)

Test_case_Acceptance_criteria  \
0  [Weekly, Ad, -, tap, on, any, product, offer, ...   
1  [As, a, PdM,, I, want, to, ensure, that, the, ...   
2  [As, a, customer,, I, should, see, age, restri...   
3  [Verify, Banner, navigation, for, the, below, ...   
4  [Display, the, Meal, Plans, banner, based, on,...   

                                          Test_Steps  \
0  [User, logs, into, UMA, application, with, val...   
1  [Login, UMA, app, with, valid, email/, mobile,...   
2  [Login, UMA, app, with, valid, email/, mobile,...   
3  [User, logs, into, UMA, application, with, val...   
4  [User, logs, into, UMA, application, with, val...   

                                     Expected_Result  
0  [User, navigates, to, Home, page, on, UMA, app...  
1  [User, should, be, able, to, login, successful...  
2  [Your, order, contains, age-restricted, items....  
3  [User, navigates, to, Home, page, on, UMA, app...  
4  [User, navigates, to, Home, page, on, UMA, app...

In [12]:
stop_words = set(stopwords.words('english'))

# Function to remove stopwords
def remove_stopwords(tokens):
    return [token for token in tokens if token.lower() not in stop_words]

# Apply stopwords removal
df['Test_case_Acceptance_criteria'] = df['Test_case_Acceptance_criteria'].apply(remove_stopwords)
df['Test_Steps'] = df['Test_Steps'].apply(remove_stopwords)
df['Expected_Result'] = df['Expected_Result'].apply(remove_stopwords)

# Inspect the data after stopwords removal
df.head(5)

Test_case_Acceptance_criteria  \
0  [Weekly, Ad, -, tap, product, offer, -, tap, A...   
1  [PdM,, want, ensure, L2, entry, points, workin...   
2  [customer,, see, age, restriction, message, ch...   
3  [Verify, Banner, navigation, banners, places, ...   
4  [Display, Meal, Plans, banner, based, banner.,...   

                                          Test_Steps  \
0  [User, logs, UMA, application, valid, user's, ...   
1  [Login, UMA, app, valid, email/, mobile, no., ...   
2  [Login, UMA, app, valid, email/, mobile, no., ...   
3  [User, logs, UMA, application, valid, user's, ...   
4  [User, logs, UMA, application, valid, user's, ...   

                                     Expected_Result  
0  [User, navigates, Home, page, UMA, application...  
1  [User, able, login, successfully, home, page, ...  
2  [order, contains, age-restricted, items., Some...  
3  [User, navigates, Home, page, UMA, application...  
4  [User, navigates, Home, page, UMA, application...

In [14]:
lemmatizer = WordNetLemmatizer()

# Function to lemmatize tokens
def lemmatize_tokens(tokens):
    return [lemmatizer.lemmatize(token, pos = 'v') for token in tokens]

# Apply lemmatization
df['Test_case_Acceptance_criteria'] = df['Test_case_Acceptance_criteria'].apply(lemmatize_tokens)
df['Test_Steps'] = df['Test_Steps'].apply(lemmatize_tokens)
df['Expected_Result'] = df['Expected_Result'].apply(lemmatize_tokens)

# Inspect the data after lemmatization
df.head(5)

Test_case_Acceptance_criteria  \
0  [Weekly, Ad, -, tap, product, offer, -, tap, A...   
1  [PdM,, want, ensure, L2, entry, point, work, f...   
2  [customer,, see, age, restriction, message, ch...   
3  [Verify, Banner, navigation, banner, place, di...   
4  [Display, Meal, Plans, banner, base, banner., ...   

                                          Test_Steps  \
0  [User, log, UMA, application, valid, user's, c...   
1  [Login, UMA, app, valid, email/, mobile, no., ...   
2  [Login, UMA, app, valid, email/, mobile, no., ...   
3  [User, log, UMA, application, valid, user's, c...   
4  [User, log, UMA, application, valid, user's, c...   

                                     Expected_Result  
0  [User, navigate, Home, page, UMA, application....  
1  [User, able, login, successfully, home, page, ...  
2  [order, contain, age-restricted, items., Someo...  
3  [User, navigate, Home, page, UMA, application,...  
4  [User, navigate, Home, page, UMA, application....

In [15]:
all_tokens = df['Test_case_Acceptance_criteria'].tolist() + df['Test_Steps'].tolist() + df['Expected_Result'].tolist()

# Train the Word2Vec model
word2vec_model = Word2Vec(sentences=all_tokens, vector_size=100, window=5, min_count=1, sg=0)

# Function to get embeddings for tokens
def get_embeddings(tokens, model):
    embeddings = []
    for token in tokens:
        if token in model.wv:
            embeddings.append(model.wv[token])
        else:
            embeddings.append(np.zeros(model.vector_size))  # Handle out-of-vocabulary words
    return np.mean(embeddings, axis=0)  # Mean vector for the document

# Apply the function to each column
df['Acceptance_criteria_embeddings'] = df['Test_case_Acceptance_criteria'].apply(lambda tokens: get_embeddings(tokens, word2vec_model) if tokens else np.nan)
df['Test_Steps_embeddings'] = df['Test_Steps'].apply(lambda tokens: get_embeddings(tokens, word2vec_model) if tokens else np.nan)
df['Expected_Result_embeddings'] = df['Expected_Result'].apply(lambda tokens: get_embeddings(tokens, word2vec_model) if tokens else np.nan)

# Verify the final DataFrame
df.head(5)

Test_case_Acceptance_criteria  \
0  [Weekly, Ad, -, tap, product, offer, -, tap, A...   
1  [PdM,, want, ensure, L2, entry, point, work, f...   
2  [customer,, see, age, restriction, message, ch...   
3  [Verify, Banner, navigation, banner, place, di...   
4  [Display, Meal, Plans, banner, base, banner., ...   

                                          Test_Steps  \
0  [User, log, UMA, application, valid, user's, c...   
1  [Login, UMA, app, valid, email/, mobile, no., ...   
2  [Login, UMA, app, valid, email/, mobile, no., ...   
3  [User, log, UMA, application, valid, user's, c...   
4  [User, log, UMA, application, valid, user's, c...   

                                     Expected_Result  \
0  [User, navigate, Home, page, UMA, application....   
1  [User, able, login, successfully, home, page, ...   
2  [order, contain, age-restricted, items., Someo...   
3  [User, navigate, Home, page, UMA, application,...   
4  [User, navigate, Home, page, UMA, application....   

                      Acceptance_criteria_embeddings  \
0  [2.9078821e-05, 0.0009868374, 0.0006897929, 0....   
1  [4.9687253e-05, -0.0002648631, -0.0011476703, ...   
2  [-0.0019043502, -0.0007733393, -0.00047627056,...   
3  [0.00079187436, 0.001024591, -0.00025014183, -...   
4  [0.0006987122, 0.0025012388, 0.00094601634, -0...   

                               Test_Steps_embeddings  \
0  [-0.00090376585, 0.0015351841, 0.00077817513, ...   
1  [-0.0007915226, 0.0008593759, 0.00056966604, -...   
2  [-0.0010107799, -0.0004325275, 0.0025766247, 0...   
3  [-0.00082380656, 0.0015335361, 0.0008829938, 0...   
4  [-0.0006520124, 0.00076459144, 0.0014451812, 0...   

                          Expected_Result_embeddings  
0  [-0.00075740286, 0.0017703008, 7.018649e-05, 0...  
1  [0.00035405744, 0.0019673503, -0.00071650144, ...  
2  [-0.0022062701, -0.0032818727, 0.0012025184, -...  
3  [-0.0007905865, 0.0017265088, 0.00018967084, 0...  
4  [-0.00028285536, 0.0013591949, -0.00073397934,...

In [16]:
df = df.drop(['Test_case_Acceptance_criteria', 'Test_Steps', 'Expected_Result'], axis = 1)
df.head(5)

Acceptance_criteria_embeddings  \
0  [2.9078821e-05, 0.0009868374, 0.0006897929, 0....   
1  [4.9687253e-05, -0.0002648631, -0.0011476703, ...   
2  [-0.0019043502, -0.0007733393, -0.00047627056,...   
3  [0.00079187436, 0.001024591, -0.00025014183, -...   
4  [0.0006987122, 0.0025012388, 0.00094601634, -0...   

                               Test_Steps_embeddings  \
0  [-0.00090376585, 0.0015351841, 0.00077817513, ...   
1  [-0.0007915226, 0.0008593759, 0.00056966604, -...   
2  [-0.0010107799, -0.0004325275, 0.0025766247, 0...   
3  [-0.00082380656, 0.0015335361, 0.0008829938, 0...   
4  [-0.0006520124, 0.00076459144, 0.0014451812, 0...   

                          Expected_Result_embeddings  
0  [-0.00075740286, 0.0017703008, 7.018649e-05, 0...  
1  [0.00035405744, 0.0019673503, -0.00071650144, ...  
2  [-0.0022062701, -0.0032818727, 0.0012025184, -...  
3  [-0.0007905865, 0.0017265088, 0.00018967084, 0...  
4  [-0.00028285536, 0.0013591949, -0.00073397934,...

In [17]:
X = np.array(df['Acceptance_criteria_embeddings'].tolist())
y_test_steps = np.array(df['Test_Steps_embeddings'].tolist())
y_expected_result = np.array(df['Expected_Result_embeddings'].tolist())

# Reshape data for LSTM: (samples, timesteps, features)
X = X.reshape((X.shape[0], 1, X.shape[1]))
y_test_steps = y_test_steps.reshape((y_test_steps.shape[0], 1, y_test_steps.shape[1]))
y_expected_result = y_expected_result.reshape((y_expected_result.shape[0], 1, y_expected_result.shape[1]))

# Split the data into training and testing sets
X_train, X_test, y_train_test_steps, y_test_test_steps = train_test_split(X, y_test_steps, test_size=0.2, random_state=42)
_, _, y_train_expected_result, y_test_expected_result = train_test_split(X, y_expected_result, test_size=0.2, random_state=42)

In [18]:
from tensorflow.keras.layers import LSTM, Dense, TimeDistributed

# Define the model for Test Steps
model_test_steps = Sequential([
    LSTM(50, activation='relu', input_shape=(X_train.shape[1], X_train.shape[2]), return_sequences=True),
    TimeDistributed(Dense(X_train.shape[2]))
])

model_test_steps.compile(optimizer='adam', loss='mse')

# Define the model for Expected Result
model_expected_result = Sequential([
    LSTM(50, activation='relu', input_shape=(X_train.shape[1], X_train.shape[2]), return_sequences=True),
    TimeDistributed(Dense(X_train.shape[2]))
])

model_expected_result.compile(optimizer='adam', loss='mse')

/Users/preethamreddygollapalli/anaconda3/lib/python3.11/site-packages/keras/src/layers/rnn/rnn.py:204: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)


In [19]:
# Train the model for Test Steps
model_test_steps.fit(X_train, y_train_test_steps, epochs=10, batch_size=32, validation_split=0.2)

# Train the model for Expected Result
model_expected_result.fit(X_train, y_train_expected_result, epochs=10, batch_size=32, validation_split=0.2)

Epoch 1/10
1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 533ms/step - loss: 2.2174e-06 - val_loss: 9.4766e-07
Epoch 2/10
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 13ms/step - loss: 1.0551e-06 - val_loss: 6.0476e-07
Epoch 3/10
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step - loss: 8.6695e-07 - val_loss: 6.1300e-07
Epoch 4/10
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step - loss: 9.7589e-07 - val_loss: 6.2904e-07
Epoch 5/10
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step - loss: 1.0319e-06 - val_loss: 6.0141e-07
Epoch 6/10
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step - loss: 9.9991e-07 - val_loss: 5.6963e-07
Epoch 7/10
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 27ms/step - loss: 9.3908e-07 - val_loss: 5.5550e-07
Epoch 8/10
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step - loss: 8.8153e-07 - val_loss: 5.5216e-07
Epoch 9/10
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step - loss: 8.3433e-07 - val_loss: 5.5272e-07
Epoch 10/10
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step - loss: 8.0194e-07 - val_loss: 5.5084e-07
Epoch 1/10
1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 617ms/step - loss: 2.4237e-06 - val_loss: 1.0210e

In [20]:
mse_test_steps = model_test_steps.evaluate(X_test, y_test_test_steps, verbose=0)
print(f'Mean Squared Error for Test Steps: {mse_test_steps}')

# Evaluate the model for Expected Result
mse_expected_result = model_expected_result.evaluate(X_test, y_test_expected_result, verbose=0)
print(f'Mean Squared Error for Expected Result: {mse_expected_result}')

Mean Squared Error for Test Steps: 2.547742951719556e-06
Mean Squared Error for Expected Result: 1.5647674445062876e-06


In [21]:
new_acceptance_criteria = df['Acceptance_criteria_embeddings'].tolist()[0]
new_acceptance_criteria = np.array(new_acceptance_criteria).reshape((1, 1, len(new_acceptance_criteria)))

# Make predictions
predicted_test_steps = model_test_steps.predict(new_acceptance_criteria)
predicted_expected_result = model_expected_result.predict(new_acceptance_criteria)

print(f'Predicted Test Steps Embeddings: {predicted_test_steps}')
print(f'Predicted Expected Result Embeddings: {predicted_expected_result}')

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 63ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 46ms/step
Predicted Test Steps Embeddings: [[[-8.4391527e-04  8.3808292e-04  9.2794985e-04  6.3661160e-04
    1.4777145e-04 -4.8993941e-04  6.3069363e-04  2.0756002e-03
   -8.7469915e-04 -1.1720757e-03 -6.2859093e-04 -9.6428773e-04
    1.0144784e-03 -6.3690939e-05 -3.8700749e-04 -7.1150030e-04
    5.5333151e-04  9.2034061e-05 -1.0463977e-03 -5.2145477e-03
    8.5559912e-04 -5.3791492e-04  2.6520165e-03 -8.6638553e-04
   -7.5741264e-04  5.9628719e-04 -6.6239189e-04 -8.7471894e-04
   -9.9208625e-04  8.2071731e-04  4.4646338e-04  8.4726338e-04
    9.5180282e-04 -8.4265345e-04 -5.4202758e-04  1.6481500e-03
   -2.2101693e-04 -9.7025535e-04 -6.7334180e-04 -2.8382645e-03
    6.2619505e-04 -1.0893656e-03 -8.7078079e-04 -2.0926578e-04
    8.1423775e-04  8.4379961e-04 -1.6668448e-04 -9.9032815e-04
    9.5974747e-04  8.5376378e-05  6.4395380e-04 -2.3663426e-03
   -7.3024776e-04  4.5859173e-04 -1.1602787e-03  5.6848535e-04
    2.601

In [24]:
mae_test_steps = MeanAbsoluteError()
mae_expected_result = MeanAbsoluteError()

In [25]:
y_pred_test_steps = model_test_steps.predict(X_test)
y_pred_expected_result = model_expected_result.predict(X_test)

# Calculate MAE for Test Steps
mae_test_steps_value = mae_test_steps(y_test_test_steps, y_pred_test_steps).numpy()
print(f'Mean Absolute Error for Test Steps: {mae_test_steps_value}')

# Calculate MAE for Expected Result
mae_expected_result_value = mae_expected_result(y_test_expected_result, y_pred_expected_result).numpy()
print(f'Mean Absolute Error for Expected Result: {mae_expected_result_value}')

# Calculate R-squared for Test Steps
r2_test_steps = r2_score(y_test_test_steps.flatten(), y_pred_test_steps.flatten())
print(f'R-squared for Test Steps: {r2_test_steps}')

# Calculate R-squared for Expected Result
r2_expected_result = r2_score(y_test_expected_result.flatten(), y_pred_expected_result.flatten())
print(f'R-squared for Expected Result: {r2_expected_result}')

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step
Mean Absolute Error for Test Steps: 0.0012983311899006367
Mean Absolute Error for Expected Result: 0.0009957090951502323
R-squared for Test Steps: 0.13273363428637874
R-squared for Expected Result: 0.1580453613077316
